![](ubc_header.png)

# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang, CFFS Data Analyst
****

## Part I: Data Preprocessing

## Set up and Import Libraries

In [1]:
#pip install -r requirements.txt

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest

C:\Users\smvan\anaconda3\lib\site-packages\pdpipe\col_generation.py:12: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
# Changed the path here, May 2nd 2023
# Set the root path, change the the current working directory into the project folder
path = "C:/Users/smvan/CFFS-S23/CFFS-22-23"
# path = os.getcwd()

# os.chdir is used to change the current directory to the specified path
os.chdir(path)
print(path)

C:/Users/smvan/CFFS-S23/CFFS-22-23


In [4]:
# Enable reading data table in the scrolling window if you prefer
pd.set_option("display.max_rows", None, "display.max_columns", None)

****

## Load Data Files

### Set Data File Path

In [5]:
# Select data file path for the chosen venue and time range where the recipes data stored

# Totem 2019
# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "Totem 19-20*", "*.oc"))

# Gather 2019
filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "Gather 19-20*", "*.oc"))

# OK 2019
# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "OK 19-20*", "*.oc"))
# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "OK 22-23*", "*.oc"))
filepath_list

['C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather ADD ONS.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather CAL.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather DEL DES.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather DIM SUM.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather DOD.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather FF.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather FLX A.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather FLX B.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather FLX C.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather FRUIT.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19-20\\Gather Grab&Go A.oc',
 'C:\\Users\\smvan\\CFFS-S23\\CFFS-22-23\\data\\raw\\Gather 19

### Import Items List

In [6]:
# Read items.xml files in the filepath_list and construct a dataframe
ItemId = []
Description = []
CaseQty = []
CaseUOM = []
PakQty = []
PakUOM = []
InventoryGroup = []


# from the items xml file, findtext of CaseQty, CaseUOM, PakQty, PakUOM, and InventoryGroup
# then append it on the lists above

for filepath in filepath_list:
    path = filepath + '/items.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for item in xtree.iterfind('Item'):
            ItemId.append(item.attrib['id'])
            Description.append(item.findtext('Description'))
            CaseQty.append(item.findtext('CaseQty'))
            CaseUOM.append(item.findtext('CaseUOM'))
            PakQty.append(item.findtext('PakQty'))
            PakUOM.append(item.findtext('PakUOM'))
            InventoryGroup.append(item.findtext('InventoryGroup'))

            
# Create a dataframe from the lists created above.
        
Items = pd.DataFrame({'ItemId': ItemId, 'Description': Description, 'CaseQty': CaseQty, 
                      'CaseUOM': CaseUOM, 'PakQty': PakQty, 'PakUOM': PakUOM, 'InventoryGroup': InventoryGroup}
                    )
Items.drop_duplicates(inplace=True)

Items.reset_index(drop=True, inplace=True)

In [7]:
Items

ItemId                     Description    CaseQty CaseUOM     PakQty  \
0     I-4507                         BANANA      40.000      lb      2.000   
1    I-13635                     CABBAGE UBC      1.000      lb      1.000   
2     I-4574   CARROTS SHREDDED 1/8 (COARSE)      5.000      lb      1.000   
3     I-7953            CHEESE BLUE CRUMBLED      2.000   BLOCK      2.000   
4    I-14181          CHEESE CHED SLICED 14G     24.000     bag     18.000   
5     I-3623        CHILI RED PPR CRUSHD SKR      8.000    each    330.000   
6     I-3237     CRACKER SODA SALTED IND TFC    500.000     pak      1.000   
7     I-4657                   GARLIC PEELED      3.000      lb      1.000   
8     I-4660                  GINGER PEELED       5.000      lb      1.000   
9    I-13800                         HAM B&R      1.000      Kg      1.000   
10    I-4341        HERB CILANTRO BUNCH 30CT     30.000      CT      1.000   
11    I-4772                 HERB PARSLEY MX      3.000   BUNCH      1.000   
12    I-7725                HERB THYME FRESH      8.000      oz      1.000   
13    I-3321       HONEY LIQUID SQUEEZE Bott      6.000      Kg      1.000   
14    I-1813           JUICE LEMON FRESH 32Z     16.000  bottle     32.000   
15    I-3348          MAYONNAISE 1/2 FAT TFC      2.000      4L      4.000   
16    I-4731        MUSHROOMS FOODSERVICE BC     10.000      lb      1.000   
17    I-3368   MUSTARD DIJON GRAINY OLD FASH      2.000    pail   4625.000   
18    I-3370               MUSTARD DIJON HOT      2.000    each   4625.000   
19    I-3387  OIL CANOLA OLIVE OIL BLEND TFC      6.000     can      3.000   
20    I-3388           OIL CANOLA ROMANO TFC      6.000     can      3.000   
21    I-2653  PASTE GARLIC RST FLVR CONC TFC      6.000      lb      1.000   
22    I-3643           PEPPER BLACK FINE TFC      1.000    each      2.267   
23    I-3642       PEPPER BLK COARSE GRD SHK      1.000      ea   2267.900   
24    I-3647         PEPPER WHITE GROUND TFC      2.500      Kg      1.000   
25    I-4787   PEPPERS JALAPENO GREEN 10 LBS      1.000      lb      1.000   
26    I-6026             SALT KOSHER WINDSOR     16.320      Kg   1000.000   
27    I-2254          SOUR CREAM CORR BOX 4L      1.000      4L      4.000   
28    I-4896       SPINACH WASHED NO STEM US      1.000     bag      2.500   
29    I-3660           SUGAR GRANULATED FINE     10.000      Kg      1.000   
30    I-3696                   VINEGAR RICE      12.000  bottle    710.000   
31    I-5983               WATER FOR RECIPES      1.000       L      1.000   
32    I-4472                      AVOCADO MX     20.000      CT      1.000   
33    I-4973             AVOCADO PULP CHUNKY      6.000    each    907.185   
34    I-3141        BASE VEG CONC LIQ G/FREE      4.000     pak    946.000   
35    I-3619         BAY LEAF WHL SHAKER TFC      8.000    each     84.000   
36    I-2567      BEAN GREEN WHL GRADE A IQF      6.000     bag      1.500   
37    I-3145                    BEANS PINTO.      6.000  LG CAN      2.840   
38    I-3149             BEANS TURTLE BLACK       6.000  LG CAN      2.840   
39    I-4521                        BEETS BC     25.000      lb      1.000   
40   I-13050                BEETS GOLDEN UBC      1.000      lb      1.000   
41   I-32246   BEETS SHREDDED MATCHSTICK RED      5.000      lb      1.000   
42    I-8060        BUTTER UNSALTED FRS 454G     25.000      ea    454.000   
43    I-4556                   CABBAGE REDBC     50.000      lb      1.000   
44    I-4569           CARROTS DICED 3/4 US"      5.000      lb      1.000   
45    I-4589                CARROTS JUMBO BC     50.000      lb      1.000   
46    I-4572         CARROTS JUMBO PEELED US     25.000      lb      1.000   
47    I-4590                CARROTS JUMBO US     50.000      lb      1.000   
48    I-4599                CELERY (36CT) US     36.000    HEAD      1.000   
49    I-4598                       CELERY US     36.000      CT      1.000   
50   I-14179  CHEESE MOZZA S

In [8]:
# creates a new array with unique ItemIds
all_id_list = Items["ItemId"].unique()

In [9]:
# None of the items are egg yolk liq
Items.loc[Items["Description"] == "Egg Yolk Liq"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [10]:
# Sumplemental option for egg, vegan option
Items.loc[Items["ItemId"] == "I-68700"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [11]:
# Gives you the list of breads
breadlist = []


# If the items in the Items list is a "LOAF", "SANDWICH", or "BREAD" then we should add it in the breadlist
# We append it onto the breadlist at position row["ItemId"]
for ind, row in Items.iterrows():
    if ("LOAF" or "SANDWICH" "BREAD") in row["Description"]:
        breadlist.append(row["ItemId"])

breadlist

['I-47962', 'I-1189', 'I-47963', 'I-11842', 'I-11664', 'I-1274', 'I-12478']

In [12]:
# Based on info below there are 486 rows and 7 columns
Items.shape

(837, 7)

In [13]:
Items.dtypes

ItemId            object
Description       object
CaseQty           object
CaseUOM           object
PakQty            object
PakUOM            object
InventoryGroup    object
dtype: object

In [14]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Items_List.csv")
Items.to_csv(path, index = False, header = True)

### Import Ingredients List

In [15]:
# Read ingredients.xml files in the filepath_list and construct a dataframe
IngredientId = []
Conversion = []
InvFactor = []
Qty = []
Recipe = []
Uom = []

# Using the Ingredients XML file, we extract attributes containing ingredients, conversion, invFactor, qty, recipe, and uom. 
# Then we append it onto the IngredientId, Coversion, InvFactor, Qty, Recipe, and Uom lists
# Then we create a dataframe using the lists created. 

for filepath in filepath_list:
    path = filepath + '/Ingredients.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Ingredient'):
            IngredientId.append(x.attrib['ingredient'])
            Conversion.append(x.attrib['conversion'])
            InvFactor.append(x.attrib['invFactor'])
            Qty.append(x.attrib['qty'])
            Recipe.append(x.attrib['recipe'])
            Uom.append(x.attrib['uom'])
    
Ingredients = pd.DataFrame({'IngredientId': IngredientId, 'Qty': Qty,'Uom': Uom, 'Conversion': Conversion, 
                      'InvFactor': InvFactor,'Recipe': Recipe}).drop_duplicates()
Ingredients.drop_duplicates(subset=["IngredientId", "Recipe"], inplace=True)

Ingredients.reset_index(drop=True, inplace=True)

In [16]:
Ingredients

IngredientId        Qty     Uom     Conversion  InvFactor   Recipe
0          I-3643    225.000       g     0.00100000     0.1837  P-18907
1          I-6026   1000.000       g     1.00000000     0.8163  P-18907
2          I-4341      1.000      CT     1.00000000     0.0182  P-26514
3          I-1813     15.000      ml     0.03381406     2.0000  P-36092
4          I-2254      2.000       L     1.00000000     0.2667  P-36092
5          I-3348      4.000       L     1.00000000     0.5333  P-36092
6          I-7953      2.000      Kg     1.00000000     0.2667  P-36092
7          I-3321    500.000      ml     0.00143287   500.0000  P-36640
8          I-3368    250.000      ml     1.00000000   250.0000  P-36640
9          I-3370    250.000      ml     1.00000000   250.0000  P-36640
10        I-13635    500.000       g     0.00220462   333.3333  P-44651
11         I-3623     14.174       g     1.00000000     9.4493  P-44651
12         I-3660      0.500       L     0.88028169     0.3333  P-44651
13         I-3696      1.000       L  1000.00000000     0.6667  P-44651
14         I-4574      1.000      Kg     2.20462000     0.6667  P-44651
15         I-4657     28.349       g     0.00220462    18.8993  P-44651
16         I-4660     28.349       g     0.00220462    18.8993  P-44651
17         I-5983      0.500       L     1.00000000     0.3333  P-44651
18         I-6026     45.000       g     1.00000000    30.0000  P-44651
19         I-4772      1.000   BUNCH     1.00000000     0.0222  P-44728
20         I-3388    125.000      ml     0.00100000    62.5000  P-46637
21         I-3642      4.000       g     1.00000000     2.0000  P-46637
22         I-6026     10.000       g     1.00000000     5.0000  P-46637
23        P-44728     60.000       g     1.00000000    30.0000  P-46637
24        P-58359      4.000      Kg     2.20462000     2.0000  P-46637
25         I-4507   1050.000       g     0.00555000     1.6154  P-50636
26         I-3696   1250.000      ml     1.00000000   147.0588  P-53336
27         I-4657    250.000       g     0.00220462    29.4118  P-53336
28        P-26514    250.000       g     1.00000000    29.4118  P-53336
29        P-50636      3.000      Kg  1000.00000000     0.3529  P-53336
30        P-53745      5.000      Kg     1.00000000     0.5882  P-53336
31         I-4787      1.000      Kg     2.20462000     1.1111  P-53745
32         I-4731     10.000      lb     1.00000000     1.0000  P-58359
33        I-13800     16.000      Kg     1.00000000     1.0323  P-61821
34         I-1813     10.000      ml     0.03381406     9.0909   P-8814
35         I-2653    114.000       g     0.00220462   103.6364   P-8814
36         I-3348      1.000       L     1.00000000     0.9091   P-8814
37         I-3647      5.000       g     0.00100000     4.5455   P-8814
38         I-6026     10.000       g     1.00000000     9.0909   P-8814
39         I-7725      4.000       g     0.03527399     3.6364   P-8814
40         I-3237      1.000     pak     1.00000000     1.0000  R-13180
41        I-14181      1.000   slice     1.00000000     1.0000  R-44764
42        P-36092      6.000      ml     0.00100000     1.0000  R-44780
43        P-36640     42.000      ml     0.00100000     1.0000  R-44780
44        P-53336      6.000      ml     0.00100000     1.0000  R-44780
45         P-8814      6.000      ml     0.00100000     1.0000  R-44780
46         I-3387      1.000      ml     0.00100000     1.0000  R-45468
47         I-4896     30.000       g     0.00220462     1.0000  R-45468
48        P-18907      2.000       g     1.00000000     1.0000  R-45468
49        P-46637     20.000       g     0.00100000     1.0000  R-51989
50        P-44651     23.000       g     0.00100000     1.0000  R-52651
51        P-61821     28.000       g     0.00100000     1.0000  R-53406
52        I-10282      1.000      Kg     2.20462000     1.2500  P-13881
53         I-3619      5.000       g     1.00000000     0.5000  P-14161
54         I-3649     10.000       g     1.00

In [17]:
# .loc attribute is used to filter rows and columns in a DataFrame based on if IngredientId is equal to I-29389

# This information tells us whether or not multiple recipes are using the same ingredient or not. Here we can see that 
# there are 3 recipes that use the same ingredient
Ingredients.loc[Ingredients["IngredientId"] == "I-29389"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [18]:
# Create a new dataframe that takes the IngredientId and Recipe column from the Ingredients dataframe

Ingredients_sample = Ingredients[["IngredientId", "Recipe"]]
Ingredients_sample

IngredientId   Recipe
0          I-3643  P-18907
1          I-6026  P-18907
2          I-4341  P-26514
3          I-1813  P-36092
4          I-2254  P-36092
5          I-3348  P-36092
6          I-7953  P-36092
7          I-3321  P-36640
8          I-3368  P-36640
9          I-3370  P-36640
10        I-13635  P-44651
11         I-3623  P-44651
12         I-3660  P-44651
13         I-3696  P-44651
14         I-4574  P-44651
15         I-4657  P-44651
16         I-4660  P-44651
17         I-5983  P-44651
18         I-6026  P-44651
19         I-4772  P-44728
20         I-3388  P-46637
21         I-3642  P-46637
22         I-6026  P-46637
23        P-44728  P-46637
24        P-58359  P-46637
25         I-4507  P-50636
26         I-3696  P-53336
27         I-4657  P-53336
28        P-26514  P-53336
29        P-50636  P-53336
30        P-53745  P-53336
31         I-4787  P-53745
32         I-4731  P-58359
33        I-13800  P-61821
34         I-1813   P-8814
35         I-2653   P-8814
36         I-3348   P-8814
37         I-3647   P-8814
38         I-6026   P-8814
39         I-7725   P-8814
40         I-3237  R-13180
41        I-14181  R-44764
42        P-36092  R-44780
43        P-36640  R-44780
44        P-53336  R-44780
45         P-8814  R-44780
46         I-3387  R-45468
47         I-4896  R-45468
48        P-18907  R-45468
49        P-46637  R-51989
50        P-44651  R-52651
51        P-61821  R-53406
52        I-10282  P-13881
53         I-3619  P-14161
54         I-3649  P-14161
55         I-3992  P-14161
56         I-4590  P-14161
57         I-4599  P-14161
58         I-4742  P-14161
59         I-4919  P-14161
60         I-5983  P-14161
61         I-4793  P-18746
62         I-6807  P-19175
63         I-4590  P-19208
64         I-4381  P-24452
65        P-26514  P-24750
66         I-3619  P-25761
67         I-3649  P-25761
68         I-3660  P-25761
69         I-3698  P-25761
70         I-4660  P-25761
71         I-4750  P-25761
72         I-6026  P-25761
73        P-52036  P-25761
74         I-3643  P-26019
75         I-6026  P-26019
76         I-3388  P-26020
77         I-4657  P-26020
78         I-6443  P-26062
79        P-18907  P-26062
80        P-24750  P-26062
81        P-44429  P-26062
82        P-57095  P-26062
83        P-57499  P-26062
84         I-3388  P-26140
85         I-6026  P-26140
86         I-6443  P-26140
87        P-24750  P-26140
88        P-26020  P-26140
89        P-39167  P-26140
90        P-44475  P-26140
91        P-56921  P-26140
92        P-56923  P-26140
93         I-2911  P-26144
94        I-30068  P-26144
95         I-3388  P-26144
96         I-3435  P-26144
97         I-3630  P-26144
98         I-3640  P-26144
99        I-36672  P-26144
100       P-26020  P-26144
101       P-32661  P-26144
102       P-32678  P-26144
103       P-38556  P-26144
104        I-3141  P-32661
105        I-5983  P-32661
106        I-3145  P-32678
107        I-3630  P-35880
108        I-6026  P-35880
109       P-26514  P-35880
110        P-7139  P-35880
111        P-9713  P-35880
112        P-9851  P-35880
113        I-3388  P-35881
114        I-3629  P-35881
115        I-3630  P-35881
116        I-4657  P-35881
117        I-4742  P-35881
118        I-4913  P-35881
119        I-4978  P-35881
120        I-6026  P-35881
121        I-6443  P-35881
122       P-48495  P-35881
123        P-7635  P-35881
124       I-19665  P-35894
125        I-3388  P-35894
126        I-3629  P-35894
127        I-3630  P-35894
128        I-4742  P-35894
129        I-6026  P-35894
130        I-6443  P-35894
131       P-48495  P-35894
132        P-7444  P-35894
133        I-3223  P-35895
134        I-3386  P-35895
135        I-3477  P-35895
136        I-5983  P-35895
137        I-6026  P-35895
138       P-24750  P-35895
139        P-7444  P-35895
140        P-9741  P-35895
141        P-9746  P-35895
142        I-2217  P-35898
143        I-2254  P-35898
144        I-3348  P-35898
145       I-37480  P-35898
146        I-6026  P-35898
147      

In [19]:
# This will output the IngredientId on the right side and the number of times the ingredient appears in the Ingredients
# dataframe on the left side. 

# The duplicated() method returns a Series with True and False values that describe which rows in the DataFrame are 
# duplicated and not.

check = Ingredients["IngredientId"].duplicated()

# The line below tells us at which index is the ingredient duplicated. For example I-4598 exists on index 2 of the dataframe and
# then again on index 8. So duplicate is first true on index 8, which is why it is printed below. It also appears in a below 
# index so it is printed again with that index number. 
Ingredients["IngredientId"][check]

18       I-6026
22       I-6026
26       I-3696
27       I-4657
34       I-1813
36       I-3348
38       I-6026
60       I-5983
63       I-4590
65      P-26514
66       I-3619
67       I-3649
68       I-3660
70       I-4660
72       I-6026
74       I-3643
75       I-6026
76       I-3388
77       I-4657
79      P-18907
84       I-3388
85       I-6026
86       I-6443
87      P-24750
95       I-3388
100     P-26020
105      I-5983
107      I-3630
108      I-6026
109     P-26514
113      I-3388
115      I-3630
116      I-4657
117      I-4742
120      I-6026
121      I-6443
125      I-3388
126      I-3629
127      I-3630
128      I-4742
129      I-6026
130      I-6443
131     P-48495
136      I-5983
137      I-6026
138     P-24750
139      P-7444
143      I-2254
144      I-3348
146      I-6026
147      I-6443
151     P-18907
153      P-7139
154     P-24452
159     P-18907
164      I-6026
165      I-6443
168      I-4787
169      I-3630
171      I-4742
172      I-4978
175      P-7444
176     

In [20]:
# We can see from the printed items above that I-64877 does not appear because it does not get duplicated
Ingredients.loc[Ingredients["IngredientId"] == "I-64877"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [21]:
210 * 9.8315

2064.6150000000002

In [22]:
Ingredients

IngredientId        Qty     Uom     Conversion  InvFactor   Recipe
0          I-3643    225.000       g     0.00100000     0.1837  P-18907
1          I-6026   1000.000       g     1.00000000     0.8163  P-18907
2          I-4341      1.000      CT     1.00000000     0.0182  P-26514
3          I-1813     15.000      ml     0.03381406     2.0000  P-36092
4          I-2254      2.000       L     1.00000000     0.2667  P-36092
5          I-3348      4.000       L     1.00000000     0.5333  P-36092
6          I-7953      2.000      Kg     1.00000000     0.2667  P-36092
7          I-3321    500.000      ml     0.00143287   500.0000  P-36640
8          I-3368    250.000      ml     1.00000000   250.0000  P-36640
9          I-3370    250.000      ml     1.00000000   250.0000  P-36640
10        I-13635    500.000       g     0.00220462   333.3333  P-44651
11         I-3623     14.174       g     1.00000000     9.4493  P-44651
12         I-3660      0.500       L     0.88028169     0.3333  P-44651
13         I-3696      1.000       L  1000.00000000     0.6667  P-44651
14         I-4574      1.000      Kg     2.20462000     0.6667  P-44651
15         I-4657     28.349       g     0.00220462    18.8993  P-44651
16         I-4660     28.349       g     0.00220462    18.8993  P-44651
17         I-5983      0.500       L     1.00000000     0.3333  P-44651
18         I-6026     45.000       g     1.00000000    30.0000  P-44651
19         I-4772      1.000   BUNCH     1.00000000     0.0222  P-44728
20         I-3388    125.000      ml     0.00100000    62.5000  P-46637
21         I-3642      4.000       g     1.00000000     2.0000  P-46637
22         I-6026     10.000       g     1.00000000     5.0000  P-46637
23        P-44728     60.000       g     1.00000000    30.0000  P-46637
24        P-58359      4.000      Kg     2.20462000     2.0000  P-46637
25         I-4507   1050.000       g     0.00555000     1.6154  P-50636
26         I-3696   1250.000      ml     1.00000000   147.0588  P-53336
27         I-4657    250.000       g     0.00220462    29.4118  P-53336
28        P-26514    250.000       g     1.00000000    29.4118  P-53336
29        P-50636      3.000      Kg  1000.00000000     0.3529  P-53336
30        P-53745      5.000      Kg     1.00000000     0.5882  P-53336
31         I-4787      1.000      Kg     2.20462000     1.1111  P-53745
32         I-4731     10.000      lb     1.00000000     1.0000  P-58359
33        I-13800     16.000      Kg     1.00000000     1.0323  P-61821
34         I-1813     10.000      ml     0.03381406     9.0909   P-8814
35         I-2653    114.000       g     0.00220462   103.6364   P-8814
36         I-3348      1.000       L     1.00000000     0.9091   P-8814
37         I-3647      5.000       g     0.00100000     4.5455   P-8814
38         I-6026     10.000       g     1.00000000     9.0909   P-8814
39         I-7725      4.000       g     0.03527399     3.6364   P-8814
40         I-3237      1.000     pak     1.00000000     1.0000  R-13180
41        I-14181      1.000   slice     1.00000000     1.0000  R-44764
42        P-36092      6.000      ml     0.00100000     1.0000  R-44780
43        P-36640     42.000      ml     0.00100000     1.0000  R-44780
44        P-53336      6.000      ml     0.00100000     1.0000  R-44780
45         P-8814      6.000      ml     0.00100000     1.0000  R-44780
46         I-3387      1.000      ml     0.00100000     1.0000  R-45468
47         I-4896     30.000       g     0.00220462     1.0000  R-45468
48        P-18907      2.000       g     1.00000000     1.0000  R-45468
49        P-46637     20.000       g     0.00100000     1.0000  R-51989
50        P-44651     23.000       g     0.00100000     1.0000  R-52651
51        P-61821     28.000       g     0.00100000     1.0000  R-53406
52        I-10282      1.000      Kg     2.20462000     1.2500  P-13881
53         I-3619      5.000       g     1.00000000     0.5000  P-14161
54         I-3649     10.000       g     1.00

In [23]:
Ingredients.loc[Ingredients["IngredientId"] == "I-64877"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [24]:
# Below we are checking if we can extract an entire recipe. So we can do .loc with the particular recipe id and then 
# print all the data points (ingredientId, Qty, Uom, Conversion, InvFactor) for that recipe. 
Ingredients.loc[Ingredients["Recipe"] == "R-68698"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [25]:
Items.loc[Items["ItemId"] == "I-68700"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [26]:
Ingredients.shape

(4797, 6)

In [27]:
Ingredients.dtypes

IngredientId    object
Qty             object
Uom             object
Conversion      object
InvFactor       object
Recipe          object
dtype: object

In [28]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Ingredients_List.csv")
Ingredients.to_csv(path, index = False, header = True)

### Import Preps List

In [29]:
# Read preps.xml files in the filepath_list and construct a dataframe
PrepId = []
Description = []
PakQty = []
PakUOM = []
InventoryGroup = []


# Here we do the same thing for the Preps XML file where we find the columns using attrib function and then append it onto
# the dataframe called Preps. 

for filepath in filepath_list:
    path = filepath + '/Preps.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Prep'):
            PrepId.append(x.attrib['id'])
            Description.append(x.findtext('Description'))
            PakQty.append(x.findtext('PakQty'))
            PakUOM.append(x.findtext('PakUOM'))
            InventoryGroup.append(x.findtext('InventoryGroup'))
    
Preps = pd.DataFrame({'PrepId': PrepId, 'Description': Description,
                  'PakQty': PakQty, 'PakUOM':PakUOM, 'InventoryGroup': InventoryGroup}).drop_duplicates()
preps_columns = Preps.columns
Preps.drop_duplicates(subset=["PrepId"], inplace=True)

Preps.reset_index(drop=True, inplace=True)

In [30]:
Preps

PrepId                     Description    PakQty PakUOM  \
0     P-8814       Aoli- RoastedGarlic Thyme     1.100      L   
1    P-18907                 MIX|Salt&Pepper  1225.000      g   
2    P-44651                PICKLED|Farm Veg     1.500     Kg   
3    P-46637      PREP|Sauteed Mushrooms|GRL     2.000     Kg   
4    P-53336          SAUCE|Banana hot sauce     8.500      L   
5    P-36640             SAUCE|Honey Mustard     1.000      L   
6    P-36092           SAUCE|Mayo|Gorganzola     7.500      L   
7    P-58359     SLICED|Mushroom Foodservice    10.000     lb   
8    P-44728           YEILD|Chopped Parsley    45.000      g   
9    P-50636             YIELD|Banana|Peeled   650.000      g   
10   P-26514             YIELD|Cilantro|Herb    55.000      g   
11   P-61821           YIELD|Ham|1 whole ham    15.500     Kg   
12   P-53745  YIELD|Jalapenos wt seeds|Whole     0.900     Kg   
13   P-45062      BREADING|Chick Wings|GFree     7.300     Kg   
14   P-50535               BRINE|Pork|Liquid    43.000      L   
15   P-51131      BRINED|Pork Butt|Marinated     8.000     Kg   
16   P-59581           CAL|Tofu|Cumin & Lime     5.000     Kg   
17   P-40407          Caliente-Chips & Salsa     1.000    1UN   
18   P-24750                CHOPPED|Cilantro     0.500     Kg   
19    P-9852    COOKED|Butternut Squash|3/4"     1.700     Kg   
20   P-51145            COOKED|Cod|Taco Meat     0.750     Kg   
21    P-7736                   COOKED|Quinoa     5.400     Kg   
22   P-44637            COOKED|Rice|Chipotle    10.000     Kg   
23   P-35895       COOKED|Rice|Coconut Pilaf     5.000     Kg   
24   P-26144          COOKED|Rice|With Beans    12.000     Kg   
25   P-44517         Crushed Spanish Potatos     0.454     Kg   
26   P-41094               DICED|Carrot|1/4"    11.170     Kg   
27   P-41095               DICED|Celery|1/4"    13.608     Kg   
28    P-9741           DICED|Green Onion|1/8     1.000     Kg   
29    P-9746           DICED|Jumbo Onion|1/4     1.000     lb   
30   P-57499             DICED|Red Onion 1/8    11.000     Kg   
31    P-9765           DICED|Red Pepper|1/4"     1.000     Kg   
32   P-44429          DICED|Roma Tomato|1/4"     1.000     Kg   
33    P-9782               DICED|Tomato|1/4"     1.000     lb   
34   P-38556         DICED|Yellow Onion|1/4"    11.400     Kg   
35   P-39167         DICED|Yellow Onion|3/4"    11.010     Kg   
36    P-9757              DICED|Zucchini|1/4     1.000     lb   
37   P-32678            DRAINED| Pinto Beans     2.000     Kg   
38    P-7635      DRAINED|Turtle Black Beans     1.740     Kg   
39   P-43954               Elote-Corn Butter     1.000     lb   
40   P-44512                 Elote-Corn-prep    12.000   each   
41   P-55548      FRIED|Corn Tortilla Strips     0.500     Kg   
42   P-52620         GARNISH|Lime Mini Wedge     8.000  piece   
43   P-44776                   MIX|Cumin Rub   500.000      g   
44   P-26019             MIX|Salt and Pepper  1225.000      g   
45    P-7139                       OIL|Lemon     2.000      L   
46   P-25761               PICKLED|Red Onion     5.000     lb   
47    P-7637           PREP Sour Cream/Salsa     1.000   srvg   
48   P-48495            PREP|Cilantro|Minced   100.000      g   
49   P-53616             PREP|Dice jalapenos     0.900     Kg   
50    P-7444               PREP|Garlic Puree     4.000      L   
51    P-9745                PREP|Jumbo Onion    45.600     lb   
52   P-44585           PREP|Lime|WEDGE|6gram    45.000      g   
53   P-57227                   PREP|Mirepoix     4.000     Kg   
54    P-8205           PREP|Pull pork|COOKED     5.600     Kg   
55   P-40584             PREP|Shallot Crispy     9.000     Kg   
56   P-53007          PREP|Soup|Caliente new    18.000      L   
57   P-14161              PREP|Stock|Chicken    10.000      L   
58    P-9778           PREP|Tomato|Processed     0.720     Kg   
59   P-53277                  PREP|Veg Stock    10.300      L   
60   P-26020            PUREE|Garlic|Kg -

In [31]:
# This tells us that there are not any duplicates in the Preps dataframe. There is a different process|ingredient pair for 
# all the recipes. 
check = Preps["PrepId"].duplicated().any()
print(check)

False


In [32]:
# There are 546 rows and 5 columns
Preps.shape

(766, 5)

In [33]:
# Here we see there is only one place P-50739 is used in the Preps
Preps.loc[Preps["PrepId"] == "P-50739"]

Empty DataFrame
Columns: [PrepId, Description, PakQty, PakUOM, InventoryGroup]
Index: []

In [34]:
Preps.dtypes

PrepId            object
Description       object
PakQty            object
PakUOM            object
InventoryGroup    object
dtype: object

In [35]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Preps_List.csv")
Preps.to_csv(path, index = False, header = True)

### Import Products List

In [36]:
# Read products.xml files in the filepath_list and construct a dataframe
ProdId = []
Description = []
SalesGroup = []

# From the XML file for products append the id into ProdId, description into Description, and SalesGroup into SalesGroup list.
# Make a dataframe out of the 3 lists
# Then also drop the duplicates in the Products dataframe

for filepath in filepath_list:
    path = filepath + '/Products.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Prod'):
            ProdId.append(x.attrib['id'])
            Description.append(x.findtext('Description'))
            SalesGroup.append(x.findtext('SalesGroup'))
        
Products = pd.DataFrame({'ProdId': ProdId, 'Description': Description, 'SalesGroup': SalesGroup})
Products.drop_duplicates(inplace=True)

Products.reset_index(drop=True, inplace=True)

In [37]:
Products

ProdId                     Description               SalesGroup
0    R-44780        ADD|Condiment House Made                  ADD ONS
1    R-13180                    ADD|Crackers                  ADD ONS
2    R-44764            GRL|Add|Cheese|Ratio                  ADD ONS
3    R-53406                 GRL|Add|Ham|1oz                  ADD ONS
4    R-51989                GRL|Add|Mushroom                  ADD ONS
5    R-52651              GRL|Add|PickledVeg                  ADD ONS
6    R-45468                 GRL|Add|Spinach                  ADD ONS
7    R-35896     CAL|Bowl|Havana|Plant based            GV - CALIENTE
8    R-35900                 CAL|Bowl|Latino            GV - CALIENTE
9    R-46549  CAL|Quesadilla|black bean tofu    GV - CALIENTE FEATURE
10   R-44784    CAL|Side|Brown Rice Chipotle     GV - CALIENTE BRUNCH
11   R-44889          CAL|Side|Chips & Salsa            GV - CALIENTE
12   R-44515             CAL|Side|Corn Elote            GV - CALIENTE
13   R-44791              CAL|Side|Guacamole            GV - CALIENTE
14   R-47363          CAL|Side|Pico de Gallo            GV - CALIENTE
15   R-44520       CAL|Side|Potato Los Cabos     GV - CALIENTE BRUNCH
16   R-36628             CAL|Side|Rice&Beans            GV - CALIENTE
17   R-46335       CAL|Side|Spanish Potatoes            GV - CALIENTE
18   R-53289      CAL|Soup|Mexican Veggie|Sp            GV - CALIENTE
19   R-44511       CAL|Soup|Tortilla Chicken            GV - CALIENTE
20   R-50330             CAL|Taco|Chicken(1)            GV - CALIENTE
21   R-35879                 CAL|Taco|Cod(1)            GV - CALIENTE
22   R-44583           CAL|Taco|Mojo pork(1)            GV - CALIENTE
23   R-53975         FREE|Greens|Latino Bowl            GV - CALIENTE
24   R-30499          DEL|Des|Soft Serve|8oz              GV - DELISH
25   R-50538           DEL|Panini|Chick&Brie              GV - DELISH
26   R-50537    DEL|Panini|Fire roasted Farm              GV - DELISH
27   R-50308            DEL|Panini|Margarita              GV - DELISH
28   R-55095          DEL|Panini|Roasted Veg              GV - DELISH
29   R-46547                DEL|Salad|Bandit              GV - DELISH
30   R-50302        DEL|Salad|Caesar Classic              GV - DELISH
31   R-50301                 DEL|Salad|Cobb               GV - DELISH
32   R-55144                 DEL|Salad|Greek              GV - DELISH
33   R-44324        DEL|Salad|Marinated Tofu              GV - DELISH
34   R-50300             DEL|Salad|Ubc Fresh              GV - DELISH
35   R-36817             DEL|Smoothie|Delish              GV - DELISH
36   R-40466       DEL|Smoothie|Hawaiian Sun              GV - DELISH
37   R-50298             DEL|Smoothie|Nojito              GV - DELISH
38   R-36814      DEL|Smoothie|Orange Zinger              GV - DELISH
39   R-36763       DEL|Smoothie|Rise & Shine              GV - DELISH
40   R-49036      DEL|Smoothie|Strwbry Cupid              GV - DELISH
41   R-13183             DES|Bar|Granola|UBC             GV - DESSERT
42   R-39842   DES|Biscotti|Wendel's|Almond              GV - DESSERT
43   R-32329          DES|Cake|Cheesecake GF             GV - DESSERT
44   R-13852    DES|Cake|Cheesecake|New York             GV - DESSERT
45   R-13162              DES|Cake|Ponderosa             GV - DESSERT
46   R-22310             DES|Cake|Slice Asst             GV - DESSERT
47   R-13159                DES|Cinnamon Bun             GV - DESSERT
48   R-53070               DES|Cookie|3 pack             GV - DESSERT
49   R-53364               DES|Cookie|6 pack             GV - DESSERT
50   R-55318  DES|Cookie|Ed's ValentineJumbo             GV - DESSERT
51   R-13571         DES|Cookie|Supreme Asst             GV - DESSERT
52   R-54028    DES|Cookie|Uncle Ed's|4 pack             GV - DESSERT
53   R-54027    DES|Cookie|Uncle Ed's|6 pack             GV - DESSERT
54   R-55087      DES|Cookie|Valentine Heart             GV - DESSERT
55   R-55088  DES|Cookie|Valentine Raspberry             GV - DESSERT
56   R-39828    

In [38]:
# Here we can see that there is only one R-56966 in the products 
Products.loc[Products["ProdId"] == "R-56966"]

Empty DataFrame
Columns: [ProdId, Description, SalesGroup]
Index: []

In [39]:
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [40]:
# Here we can see that there is only one R-68698 in the products 
Products.loc[Products["ProdId"] == "R-68698"]

Empty DataFrame
Columns: [ProdId, Description, SalesGroup]
Index: []

In [41]:
Products.shape

(562, 3)

In [42]:
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [43]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Products_List.csv")
Products.to_csv(path, index = False, header = True)

### Import Conversions List

In [44]:
# Read conventions.xml files in the filepath_list and construct a dataframe
ConversionId = []
Multiplier = []
ConvertFromQty = []
ConvertFromUom = []
ConvertToQty = []
ConvertToUom = []

# From the XML file for Conversions append the id into ConversionId, multiplier into Multiplier, ConvertFrom->qty into 
# ConvertFromQty,ConvertFrom->uom into ConvertFromUom, ConvertTo->qty into ConvertToQty and and ConvertTo->uom into the
# CovertToUom list. 
# Make a dataframe out of the 3 lists
# Then also drop the duplicates in the Products dataframe


for filepath in filepath_list:
    path = filepath + '/Conversions.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Conversion'):
            ConversionId.append(x.attrib['id'])
            Multiplier.append(x.attrib['multiplier'])
            ConvertFromQty.append(x.find('ConvertFrom').attrib['qty'])
            ConvertFromUom.append(x.find('ConvertFrom').attrib['uom'])
            ConvertToQty.append(x.find('ConvertTo').attrib['qty'])
            ConvertToUom.append(x.find('ConvertTo').attrib['uom'])
    
    
Conversions = pd.DataFrame({'ConversionId': ConversionId, 'Multiplier': Multiplier, 'ConvertFromQty': ConvertFromQty,
                           'ConvertFromUom': ConvertFromUom, 'ConvertToQty': ConvertToQty, 'ConvertToUom': ConvertToUom}
                          ).drop_duplicates()

Conversions.reset_index(drop=True, inplace=True)

In [45]:
# Here we can see for example that to convert 1.14 L to 1 L the multiplier is 0.877 since 1/1.14 = 0.877
Conversions

ConversionId     Multiplier ConvertFromQty ConvertFromUom ConvertToQty  \
0                    1.00000000         1.0000            XXX       1.0000   
1                    0.87719298         1.0000          1.14L       1.1400   
2                    0.66666667         1.0000           1.5L       1.5000   
3                    0.57142857         1.0000         1.75 L       1.7500   
4                    0.50000000         1.0000             2L       2.0000   
5                    0.25000000         1.0000             4L       4.0000   
6                    0.08333333         1.0000           FOOT      12.0000   
7                    0.06250000         1.0000            16L      16.0000   
8                    0.05917160         1.0000         1/2LTR      16.9000   
9                    0.03937008         1.0000          750ML      25.4000   
10                   0.03333333         1.0000        KEG 30L      30.0000   
11                   0.02597403         1.0000         1140ml      38.5000   
12                   0.02500000         1.0000        full in      40.0000   
13                   0.02000000         1.0000        KEG 50L      50.0000   
14                   0.01706485         1.0000        KEG 59L      58.6000   
15                   0.01666667         1.0000           HOUR      60.0000   
16                   0.00200000         1.0000          500ML     500.0000   
17                   0.00153846         1.0000          650ML     650.0000   
18                   0.00151515         1.0000          660ML     660.0000   
19                   0.00142857         1.0000          700ML     700.0000   
20                   0.00140845         1.0000          710ml     710.0000   
21                   0.00133333         1.0000          750ML     750.0000   
22                   0.00059172         1.0000         keg50L    1690.0000   
23                   0.00050403         1.0000         keg59L    1984.0000   
24                   2.00000000         2.0000            cup       1.0000   
25                   2.00000000         2.0000             pt       1.0000   
26                   2.00000000         2.0000           Tbsp       1.0000   
27                   3.00000000         3.0000            tsp       1.0000   
28                   4.00000000         4.0000             qt       1.0000   
29                   8.00000000         8.0000          fl oz       1.0000   
30                  16.00000000        16.0000             oz       1.0000   
31                  28.34950000        28.3495              g       1.0000   
32                  29.57350000        29.5735             ml       1.0000   
33                  35.21126761       100.0000          fl oz       2.8400   
34                1000.00000000      1000.0000              g       1.0000   
35                1000.00000000      1000.0000             mg       1.0000   
36                1000.00000000      1000.0000             ml       1.0000   
37        I-1813     0.03278689         1.0000          fl oz      30.5000   
38        I-1813     0.00409836         1.0000            cup     244.0000   
39        I-2254     0.08333333         1.0000           Tbsp      12.0000   
40        I-2254     0.00434783         1.0000            cup     230.0000   
41        I-3237     0.16666667         1.0000            pak       6.0000   
42        I-3321     0.00294985         1.0000            cup     339.0000   
43        I-3348     0.06666667         1.0000           Tbsp      15.0000   
44        I-3370     0.00401606         1.0000            cup     249.0000   
45        I-3387     1.00000000         1.0000              L       1.0000   
46        I-3387     0.22222222         1.0000            tsp       4.5000   
47        I-3387     0.07142857         1.0000           Tbsp      14.0000   
48        I-3387     0.00458716         1.0000            cup     218.0000   
49        I-3388     0.22222222         1.0000            tsp       4.5000   
50        I-3388     0.071

In [46]:
# Here we can check that there are no ingredients listed since 
Conversions.loc[Conversions["ConversionId"] == "I-4582"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [47]:
all_id_list = Items["ItemId"].unique()
all_conv_list = Conversions["ConversionId"].unique()

print("All unique IDs list\n")
print(all_id_list)
print("\n")
print("All unique Conversions list\n")
print(all_conv_list)

All unique IDs list

['I-4507' 'I-13635' 'I-4574' 'I-7953' 'I-14181' 'I-3623' 'I-3237' 'I-4657'
 'I-4660' 'I-13800' 'I-4341' 'I-4772' 'I-7725' 'I-3321' 'I-1813' 'I-3348'
 'I-4731' 'I-3368' 'I-3370' 'I-3387' 'I-3388' 'I-2653' 'I-3643' 'I-3642'
 'I-3647' 'I-4787' 'I-6026' 'I-2254' 'I-4896' 'I-3660' 'I-3696' 'I-5983'
 'I-4472' 'I-4973' 'I-3141' 'I-3619' 'I-2567' 'I-3145' 'I-3149' 'I-4521'
 'I-13050' 'I-32246' 'I-8060' 'I-4556' 'I-4569' 'I-4589' 'I-4572' 'I-4590'
 'I-4599' 'I-4598' 'I-14179' 'I-3992' 'I-19665' 'I-3622' 'I-3217' 'I-3223'
 'I-49251' 'I-3629' 'I-4623' 'I-4978' 'I-2217' 'I-6832' 'I-3630' 'I-3632'
 'I-51440' 'I-2613' 'I-4508' 'I-4919' 'I-6443' 'I-10282' 'I-4712' 'I-5003'
 'I-3386' 'I-6006' 'I-3639' 'I-4742' 'I-4743' 'I-4375' 'I-17150' 'I-6807'
 'I-4750' 'I-4381' 'I-4764' 'I-2911' 'I-3640' 'I-5978' 'I-37480' 'I-3435'
 'I-3447' 'I-3449' 'I-3649' 'I-30068' 'I-4833' 'I-4793' 'I-30101' 'I-3851'
 'I-4818' 'I-3588' 'I-3779' 'I-36672' 'I-3477' 'I-4852' 'I-3494' 'I-3497'
 'I-12176' 'I-3

In [48]:
# Here we have the number of items in the list that are a part of the "all_id_list" but not part of the "all_conv_list"
missing_conv_id = []

for item in all_id_list:
    if item not in all_conv_list:
        missing_conv_id.append(item)
        
missing_conv_id
print(len(missing_conv_id))

651


In [49]:
Conversions.shape

(349, 6)

In [50]:
Conversions.loc[Conversions["ConversionId"] == "I-29389"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [51]:
Conversions.dtypes

ConversionId      object
Multiplier        object
ConvertFromQty    object
ConvertFromUom    object
ConvertToQty      object
ConvertToUom      object
dtype: object

In [52]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Conversions_List.csv")
Conversions.to_csv(path, index = False, header = True)

***
## Data Summary

In [53]:
# Summary of raw data imported for evaluation
# Here we have a summary of the number of items, preps, ingredients, products, conversions

datasum = pd.DataFrame([Items.shape, Preps.shape, Ingredients.shape, Products.shape, Conversions.shape],
                       columns = ['count', 'columns'], 
                       index = ['Items', 'Preps', 'Ingredients', 'Products', 'Conversions'])
datasum

count  columns
Items          837        7
Preps          766        5
Ingredients   4797        6
Products       562        3
Conversions    349        6